In [2]:
from transformers import AutoTokenizer, TFAutoModel
biobert_tokenizer = AutoTokenizer.from_pretrained("cambridgeltl/BioRedditBERT-uncased")

biobert_model = TFAutoModel.from_pretrained("cambridgeltl/BioRedditBERT-uncased")

Some weights of the PyTorch model were not used when initializing the TF 2.0 model TFBertModel: ['embeddings.position_ids']
- This IS expected if you are initializing TFBertModel from a PyTorch model trained on another task or with another architecture (e.g. initializing a TFBertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from a PyTorch model that you expect to be exactly identical (e.g. initializing a TFBertForSequenceClassification model from a BertForSequenceClassification model).
All the weights of TFBertModel were initialized from the PyTorch model.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFBertModel for predictions without further training.


In [8]:
import tensorflow as tf

In [1]:
import pandas as pd
train=pd.read_csv('train_data_chatbot.csv')
validation=pd.read_csv('validation_data_chatbot.csv')
print(validation.shape)

(11901, 4)


In [2]:
train=train.head(10000)
validation=validation.head(1000)

In [8]:
pd.set_option('display.max_colwidth', None)
pd.set_option("display.max_rows",None)

train.head(300)

short_question  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     can an antibiotic through an iv give you a rash a couple days later   
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     can you test positive from having the hep b vaccine   
2                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             what are the dietary restrictions for celiac disease gluten   
3                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  can i transmit genital warts seventeen years after having them removed   
4                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               is all vitamin d the same   
5                                                                            

In [3]:
questions=train['short_question']
answers=train['short_answer']
labels=train['label']


In [12]:

#https://blog.tensorflow.org/2019/05/transformer-chatbot-tutorial-with-tensorflow-2.html
#Setting Max_length to be 512 as discussed above
MAX_LENGTH = 256
import tensorflow as tf


# Tokenize, filter and pad sentences
def tokenize_and_filter(questions, answers):
  tokenized_questions, tokenized_answers = [], []
  
  for (question, answer) in zip(questions, answers):
    # generating sequences
    tokenized_question =  biobert_tokenizer.encode(question)
    tokenized_answer = biobert_tokenizer.encode(answer)
    tokenized_questions.append(tokenized_question)
    tokenized_answers.append(tokenized_answer)

  # padding the sequences
  tokenized_questions = tf.keras.preprocessing.sequence.pad_sequences(
      tokenized_questions, maxlen=MAX_LENGTH, padding='post')
  tokenized_answers = tf.keras.preprocessing.sequence.pad_sequences(
      tokenized_answers, maxlen=MAX_LENGTH, padding='post')
  
  return tokenized_questions, tokenized_answers

#tokenizing and padding the train questions and answers
questions, answers = tokenize_and_filter(questions, answers)

In [12]:
questions.shape

(10000, 256)

In [13]:
answers.shape

(10000, 256)

In [13]:

#preparing the question mask and the answer mask of the train dataset
train_question_mask=[[1 if token!=0 else 0 for token in question] for question in questions]
train_answer_mask=[[1 if token!=0 else 0 for token in answer] for answer in answers]


In [14]:

#extracting the short answers and questions from the validation data
val_questions=validation['short_question']
val_answers=validation['short_answer']
val_labels=validation['label']

In [15]:

#tokenizing and padding the validation question and answers
val_questions, val_answers = tokenize_and_filter(val_questions, val_answers)

In [16]:
#preparing the question and answer mask for the validation data
val_question_mask=[[1 if token!=0 else 0 for token in question] for question in val_questions]
val_answer_mask=[[1 if token!=0 else 0 for token in answer] for answer in val_answers]

In [17]:
import tensorflow as tf
BATCH_SIZE = 2
BUFFER_SIZE = 500
dataset = tf.data.Dataset.from_tensor_slices((
    {
        'question': questions,
        'answer': answers,
        'question_mask':train_question_mask,
        'answer_mask':train_answer_mask
    },
    {
        'label': labels.values
    },
))

# dataset = dataset.cache()
dataset = dataset.shuffle(BUFFER_SIZE)
dataset = dataset.batch(BATCH_SIZE,drop_remainder=True)
dataset = dataset.prefetch(tf.data.experimental.AUTOTUNE)

In [18]:
import tensorflow as tf
BATCH_SIZE = 2
BUFFER_SIZE =500
val_dataset = tf.data.Dataset.from_tensor_slices((
    {
        'question': val_questions,
        'answer': val_answers,
        'question_mask':val_question_mask,
        'answer_mask':val_answer_mask
    },
    {
        'label': val_labels.values
    },
))

val_dataset = val_dataset.cache()
val_dataset = val_dataset.shuffle(BUFFER_SIZE)
val_dataset = val_dataset.batch(BATCH_SIZE,drop_remainder=True)
val_dataset = val_dataset.prefetch(tf.data.experimental.AUTOTUNE)

In [19]:
import tensorflow as tf
from tensorflow.keras import Sequential
from tensorflow.keras.layers import Input,Dense
from tensorflow.keras.layers import Flatten
from tensorflow.keras.layers import Embedding
from tensorflow.keras.layers import Concatenate,Conv1D,MaxPool1D,Dropout
class FFN(tf.keras.layers.Layer):
    def __init__(
            self,
            name='FFN',
            **kwargs):
        """Simple Dense wrapped with various layers
        """

        super(FFN, self).__init__(name=name, **kwargs)
        self.dropout = 0.2
        self.ffn_layer = tf.keras.layers.Dense(
            units=256,
            activation='relu',
            kernel_initializer=tf.keras.initializers.glorot_normal(seed=32),name='FC1')
        

    def call(self, inputs):
        ffn_embedding = self.ffn_layer(inputs)
        ffn_embedding = tf.keras.layers.Dropout(
            self.dropout)(ffn_embedding)
        ffn_embedding += inputs
        return ffn_embedding

In [20]:
import tensorflow as tf
from tensorflow.keras import Sequential
from tensorflow.keras.layers import Input, Dense
from tensorflow.keras.layers import Flatten
from tensorflow.keras.layers import Embedding
from tensorflow.keras.layers import Concatenate, Conv1D, MaxPool1D


class FFN(tf.keras.layers.Layer):
    def __init__(self, name='FFN', **kwargs):
        """Simple Dense wrapped with various layers"""

        super(FFN, self).__init__(name=name, **kwargs)
        self.ffn_layer = tf.keras.layers.Dense(
            units=256,
            activation='relu',
            kernel_initializer=tf.keras.initializers.glorot_normal(seed=32), name='FC1')

    def call(self, inputs):
        ffn_embedding = self.ffn_layer(inputs)
        ffn_embedding += inputs
        return ffn_embedding


In [21]:
#https://github.com/ash3n/DocProduct/blob/master/docproduct/models.py
class MedicalQAModelwithBert(tf.keras.Model):
    def __init__(
            self,
            trainable=False,
            name=''):
        super(MedicalQAModelwithBert, self).__init__(name=name)

        self.q_ffn_layer = FFN(name='q_ffn')
        self.a_ffn_layer = FFN(name='a_ffn')
        self.biobert_model=biobert_model
        self.biobert_model.trainable=trainable
        self.cos=tf.keras.layers.Dot(axes=1,normalize=True)

    def call(self, inputs):
      question_embeddings=self.biobert_model(input_ids=inputs['question'],attention_mask=inputs['question_mask']).pooler_output
      answer_embeddings=self.biobert_model(input_ids=inputs['answer'],attention_mask=inputs['answer_mask']).pooler_output
      q_ffnn=self.q_ffn_layer(question_embeddings)
      a_ffnn=self.a_ffn_layer(answer_embeddings)
      output=self.cos([q_ffnn,a_ffnn])
      return {"label":output}

In [30]:

#defining the custom metric
batch_size=1
def custom_metric_acc(y_true,y_pred):
  y_true=tf.reshape(y_true,[tf.constant(batch_size)])
  y_pred=tf.reshape(y_pred,[tf.constant(batch_size)])
  c=tf.constant(0,dtype='float32')
  d=tf.cast(tf.math.greater_equal(y_true,c),dtype='float32')
  e=tf.cast(tf.math.greater_equal(y_pred,c),dtype='float32')
  f=tf.cast(tf.math.equal(d,e),dtype='float32')
  g=tf.reduce_sum(f)
  h=tf.cast(tf.shape(f),dtype='float32')
  i=g/h
  return i

In [22]:
#defining custom callback
class custom_callback(tf.keras.callbacks.Callback):
  def on_train_begin(self, logs={}):
        ## on begin of training, we are creating a instance varible called history
        ## it is a dict with keys [loss, acc, val_loss, val_acc]
        self.history={'acc': []}

  def on_epoch_end(self, epoch, logs={}):
        self.history['acc'].append(logs.get('custom_metric_acc'))
  


        #saving the model if validation accuracy increased from previous epoch
        if  (epoch==0) or (logs.get('custom_metric_acc')>self.history['acc'][epoch-1]):
          self.model.save_weights('medical_bert_re'+str(epoch)+'/medic'+str(epoch)+'_'+str(logs.get('custom_metric_acc')))


        is_nan_values=[]
        for i in self.model.get_weights():
          is_nan_values.append(np.isnan(i).any())

        #stopping the training if weights is nan or loss is nan or inf
        if (np.array(is_nan_values).any() or (tf.math.is_nan(logs.get('loss'))) or (np.isinf(logs.get('loss')))):
          self.model.stop_training = True

In [23]:

#compiling and training the medical qa model
import tensorflow.keras.backend as K
K.set_floatx('float32')
learning_rate=5e-6
num_epochs=1
optimizer = tf.keras.optimizers.Adam(learning_rate=learning_rate)
medical_qa_model=MedicalQAModelwithBert(trainable=True)
medical_qa_model.compile(
    optimizer=optimizer, loss=tf.keras.losses.mean_squared_error)

epochs = num_epochs

medical_qa_model.fit(dataset,validation_data=val_dataset,epochs=epochs)
medical_qa_model.summary()

SystemError: <built-in method  of PyCapsule object at 0x000001D284DB0780> returned a result with an exception set

In [35]:
medical_qa_model.save("bert")

INFO:tensorflow:Assets written to: bert\assets


INFO:tensorflow:Assets written to: bert\assets


In [37]:
output_folder = "./trained_bert_model"
medical_qa_model.save(output_folder)

INFO:tensorflow:Assets written to: ./trained_bert_model\assets


INFO:tensorflow:Assets written to: ./trained_bert_model\assets


In [46]:
import tensorflow.keras.backend as K
K.set_floatx('float32')
medical_qa_model=MedicalQAModelwithBert(trainable=True)
medical_qa_model.load_weights('./medical_bert_re3/medic3_0.9177975654602051')
learning_rate=5e-6
optimizer = tf.keras.optimizers.Adam(lr=learning_rate)
medical_qa_model.compile(
    optimizer=optimizer, loss=tf.keras.losses.mean_squared_error, metrics=[custom_metric_acc])

# original_labels=[]
predicted_labels=[]
from tqdm.notebook import tqdm
for i in tqdm(range(len(val_questions))):
  predicted_labels.append(medical_qa_model.predict({'question':np.array([val_questions[i]]),'question_mask':np.array([val_question_mask[i]]),
                             'answer':np.array([val_answers[i]]),'answer_mask':np.array([val_answer_mask[i]])})['label'][0][0])

     
     

NotFoundError: Unsuccessful TensorSliceReader constructor: Failed to find any matching files for ./medical_bert_re3/medic3_0.9177975654602051

In [47]:
model = tf.keras.models.load_model("bert")

ValueError: The two structures don't have the same nested structure.

First structure: type=tuple str=(({'attention_mask': TensorSpec(shape=(None, None), dtype=tf.int32, name=None), 'input_ids': TensorSpec(shape=(None, None), dtype=tf.int32, name=None), 'token_type_ids': TensorSpec(shape=(None, None), dtype=tf.int32, name=None)}, None, None, None, None, None, None, None, None, None, None, None, None, True), {})

Second structure: type=tuple str=((TensorSpec(shape=(None, 256), dtype=tf.int32, name='input_ids'), TensorSpec(shape=(None, 256), dtype=tf.int32, name='attention_mask'), None, None, None, None, None, None, None, None, None, None, None, True), {})

More specifically: Substructure "type=dict str={'attention_mask': TensorSpec(shape=(None, None), dtype=tf.int32, name=None), 'input_ids': TensorSpec(shape=(None, None), dtype=tf.int32, name=None), 'token_type_ids': TensorSpec(shape=(None, None), dtype=tf.int32, name=None)}" is a sequence, while substructure "type=TensorSpec str=Tensor

In [48]:
restored_model = tf.saved_model.load("bert")

In [49]:
restored_model

AttributeError: '_UserObject' object has no attribute 'summary'

In [50]:

#defining the question extractor model
x1=tf.keras.layers.Input((256),name='question',dtype='int64')
x2=tf.keras.layers.Input((256),name='question_mask',dtype='int64')
q_embed=medical_qa_model.get_layer('q_ffn')(medical_qa_model.get_layer('tf_bert_model').bert(input_ids=x1,attention_mask=x2,).pooler_output)
question_extractor_model=tf.keras.Model(inputs=[x1,x2],outputs=q_embed)

In [51]:
question_extractor_model.save('question_extractor_model_2_11')

INFO:tensorflow:Assets written to: question_extractor_model_2_11\assets


INFO:tensorflow:Assets written to: question_extractor_model_2_11\assets


In [4]:
#loading the question extractor model from disk
question_extractor_model=tf.keras.models.load_model('question_extractor_model_2_11')

In [5]:

#function to extract embeddings given a question and a question mask
def question_extractor(sam_dict):
  q_embed=question_extractor_model({'question':sam_dict['question'],'question_mask':sam_dict['question_mask']})
  return q_embed
  

In [6]:
def extract_question_embed(question):
  max_length=256
  tokenized_questions=[]
  tokenized_question =  biobert_tokenizer.encode(question)
  tokenized_questions.append(tokenized_question)

  # padding the sequences
  tokenized_questions = tf.keras.preprocessing.sequence.pad_sequences(
      tokenized_questions, maxlen=max_length, padding='post')
  attention_mask=[[1 if token>0 else 0 for token in q] for q in tokenized_questions]
  return question_extractor({'question':np.array(tokenized_questions),'question_mask':np.array(attention_mask)})

In [26]:
x1=tf.keras.layers.Input((512),name='answer',dtype='int64')
x2=tf.keras.layers.Input((512),name='answer_mask',dtype='int64')
a_embed=medical_qa_model.get_layer('a_ffn')(medical_qa_model.get_layer('tf_bert_model').bert(input_ids=x1,attention_mask=x2,).pooler_output)
answer_extractor_model=tf.keras.Model(inputs=[x1,x2],outputs=a_embed)

ValueError: Exception encountered when calling layer "a_ffn" (type FFN).

in user code:

    File "C:\Users\manis\AppData\Local\Temp\ipykernel_14468\501521922.py", line 21, in call  *
        ffn_embedding += inputs

    ValueError: Dimensions must be equal, but are 256 and 768 for '{{node a_ffn/add}} = AddV2[T=DT_FLOAT](a_ffn/FC1/Relu, Placeholder)' with input shapes: [?,256], [?,768].


Call arguments received by layer "a_ffn" (type FFN):
  • inputs=tf.Tensor(shape=(None, 768), dtype=float32)

In [56]:
#saving the answer extractor model to disk
answer_extractor_model.save('answer_extractor_model_2_13')

INFO:tensorflow:Assets written to: answer_extractor_model_2_13\assets


INFO:tensorflow:Assets written to: answer_extractor_model_2_13\assets


In [57]:
answer_extractor_model=tf.keras.models.load_model('answer_extractor_model_2_13')

In [41]:
answer_extractor_model=tf.keras.models.load_model('answer_extractor_model_2_13')

In [66]:
#function to extract embeddings given an answer and an answer mask
def answer_extractor(sam_dict):
  a_embed=answer_extractor_model({'answer':sam_dict['answer'],'answer_mask':sam_dict['answer_mask']})
  return a_embed

  

In [67]:

#defining function to extract answer embeddings
def extract_answer_embed(answer):
  max_length=512
  tokenized_answers=[]
  tokenized_answer =  biobert_tokenizer.encode(answer)
  tokenized_answers.append(tokenized_answer)

  # padding the sequences
  tokenized_answers = tf.keras.preprocessing.sequence.pad_sequences(
      tokenized_answers, maxlen=max_length, padding='post')
  attention_mask=[[1 if token>0 else 0 for token in q] for q in tokenized_answers]
  return answer_extractor({'answer':np.array(tokenized_answers),'answer_mask':np.array(attention_mask)})

In [68]:

#extracting the original(without negative sampling) train dataset
pos_train=train[train.label==1.0].copy()
pos_train.shape

(5003, 4)

In [69]:
#extracting the original(without negative sampling) validation dataset
pos_validation=validation[validation.label==1.0].copy()
pos_validation.shape

(504, 4)

In [70]:
import numpy as np
#extracting the question embeddings of train data
from tqdm.notebook import tqdm
tqdm.pandas()
pos_train['short_question_embed']=pos_train.short_question.progress_apply(lambda x: extract_question_embed(x))

  0%|          | 0/5003 [00:00<?, ?it/s]

In [71]:
#extracting the question embeddings of validation data
pos_validation['short_question_embed']=pos_validation.short_question.progress_apply(lambda x: extract_question_embed(x))

  0%|          | 0/504 [00:00<?, ?it/s]

In [72]:

#extracting the answer embeddings of train data
pos_train['short_answer_embed']=pos_train.short_answer.progress_apply(lambda x: extract_answer_embed(x))

  0%|          | 0/5003 [00:00<?, ?it/s]

In [75]:
#extracting the answer embeddings of validation data
pos_validation['short_answer_embed']=pos_validation.short_answer.progress_apply(lambda x: extract_answer_embed(x))

  0%|          | 0/504 [00:00<?, ?it/s]

short_question  \
0     can an antibiotic through an iv give you a ras...   
1     can you test positive from having the hep b va...   
2     what are the dietary restrictions for celiac d...   
8     i have had a pneumonia shot can i get either a...   
10    my baby ate her on poop my baby ate poop 4 day...   
...                                                 ...   
9986    my 18 month old has a cough what can i give her   
9991  after i have been diagnosed with an std and tr...   
9993  i have had lumps and white discoloration on my...   
9994  i had a 10days spotting before menstruation re...   
9995                             is shingles contagious   

                                           short_answer  \
0     yes it can even after you have finished the pr...   
1     test positive for what if you had a hep b vacc...   
2     omitting gluten from the diet is the key to co...   
8     you can always catch an illness from a child b...   
10    hi one of ours did that she is now 47 and a mu...   
...                                                 ...   
9986  medications sold over the counter for cough wo...   
9991  i think it would be a very good idea to be tes...   
9993  hi possible causes are sever iron deficiency p...   
9994  hi is this spotting fresh blood being very red...   
9995  i have the beginning symtoms of shingles what ...   

                                                   tags  label  \
0                                 ['rash' 'antibiotic']    1.0   
1                                       ['hepatitis b']    1.0   
2                                    ['celiac disease']    1.0   
8             ['pneumonia' 'sinus infection' 'walking']    1.0   
10           ['baby' 'cough' 'fever' 'coldness' 'cold']    1.0   
...                                                 ...    ...   
9986                                               ['']    1.0   
9991  ['sexual intercourse' 'bacterial vaginosis' 's...    1.0   
9993                              ['coughing up blood']    1.0   
9994                           ['spotting' 'pregnancy']    1.0   
9995                                       ['shingles']    1.0   

                                   short_question_embed  \
0     ((tf.Tensor(-0.35846186, shape=(), dtype=float...   
1     ((tf.Tensor(-0.38160247, shape=(), dtype=float...   
2     ((tf.Tensor(-0.39959115, shape=(), dtype=float...   
8     ((tf.Tensor(-0.14158653, shape=(), dtype=float...   
10    ((tf.Tensor(-0.16533498, shape=(), dtype=float...   
...                                                 ...   
9986  ((tf.Tensor(-0.35960472, shape=(), dtype=float...   
9991  ((tf.Tensor(-0.16135357, shape=(), dtype=float...   
9993  ((tf.Tensor(-0.32682967, shape=(), dtype=float...   
9994  ((tf.Tensor(-0.13654584, shape=(), dtype=float...   
9995  ((tf.Tensor(-0.41636616, shape=(), dtype=float...   

                                     short_answer_embed  
0     ((tf.Tensor(-0.18886898, shape=(), dtype=float...  
1     ((tf.Tensor(0.055377316, shape=(), dtype=float...  
2     ((tf.Tensor(-0.14614785, shape=(), dtype=float...  
8     ((tf.Tensor(-0.072335556, shape=(), dtype=floa...  
10    ((tf.Tensor(-0.11773818, shape=(), dtype=float...  
...                                                 ...  
9986  ((tf.Tensor(0.116145425, shape=(), dtype=float...  
9991  ((tf.Tensor(-0.032036718, shape=(), dtype=floa...  
9993  ((tf.Tensor(-0.1422489, shape=(), dtype=float3...  
9994  ((tf.Tensor(-0.1708775, shape=(), dtype=float3...  
9995  ((tf.Tensor(-0.35478535, shape=(), dtype=float...  

[5003 rows x 6 columns]

In [76]:
#converting embeddings from tensors to numpy arrays
pos_train['short_answer_embed_numpy']=pos_train.short_answer_embed.apply(lambda x: x.numpy() )
pos_train['short_question_embed_numpy']=pos_train.short_question_embed.apply(lambda x: x.numpy())

In [77]:

#converting embeddings from tensors to numpy arrays
pos_validation['short_answer_embed_numpy']=pos_validation.short_answer_embed.apply(lambda x: x.numpy() )
pos_validation['short_question_embed_numpy']=pos_validation.short_question_embed.apply(lambda x: x.numpy())

In [79]:

#Saving train question and answer embeddings to disk
pos_train.drop(['short_answer_embed','short_question_embed'],axis=1).to_csv('re_train_embeds.csv',index=False)

In [78]:
pos_validation.drop(['short_answer_embed','short_question_embed'],axis=1).to_csv('re_validation_embeds.csv',index=False)

In [9]:
df=pd.read_csv("re_train_embeds.csv")

In [11]:
df1=df[['short_question','short_answer']]

In [18]:
df1.sample(1000)

short_question  \
3417                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         what should i do if i suspect an overdose of alprazolam intensol   
2413                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 my daughter faints usually happens when she is taking a shower tests did not show anything to explain it   
1762                                        

In [ ]:
what are some of the benefits of regular exercise
what causes and who is at risk for brain tumors
is it normal for a patient to have anxiety when having an uncurable severe illness
does vitamin c impact the bodies ability to fight the common cold
how can i get started with exercise
what vitamins help migraines
what can i use for dark circles under my eyes
is it possible to ever get off the blood pressure medication